# Le bogo-tri

Marc Lorenzi

7 juillet 2022

In [ ]:
import random
import math
import matplotlib.pyplot as plt

In [ ]:
plt.rcParams['figure.figsize'] = (10, 6)

$$\newcommand\N{\mathbb N}$$
$$\newcommand\too{\longrightarrow}$$
$$\newcommand\Pr{\mathbb P}$$
$$\renewcommand\epsilon{\varepsilon}$$

## 1. L'algorithme

### 1.1 C'est quoi le bogo-tri ?

Le bogo-tri, appelé aussi tri stupide, tri du singe, etc., est un algorithme de tri. Il fonctionne de la façon suivante. Soit $s$ une liste à trier.

**Algorithme** : tant que $s$ n'est pas triée, mélanger $s$.

On peut difficilement faire plus simple. On peut aussi difficilement faire pire.

### 1.2 Le code Python

La fonction `est_triee` prend en paramètre une liste $s$ (disons une liste d'entiers). Elle renvoie `True` si la liste est triée et `False` sinon. Pour une liste $s$ de longueur $n$, la fonction effectue au plus $n-1$ comparaisons d'éléments de la liste.

In [ ]:
def est_triee(s):
    n = len(s)
    for k in range(n - 1):
        if s[k] > s[k + 1]: return False
    return True

La fonction `melanger` prend en paramètre une liste $s$ et mélange la liste sur place. Cette fonction utilise l'algorithme de Fisher-Yates que nous ne décrirons pas ici. Toutes les permutations de la liste $s$ sont obtenues avec la même probabilité. La fonction `melanger` effectue $n$ échanges d'éléments de liste sur une liste de longueur $n$.

In [ ]:
def melanger(s):
    n = len(s)
    for k in range(n):
        i = random.randint(k, n - 1)
        s[k], s[i] = s[i], s[k]

Pour pouvoir faire des tests, voici une fonction `random_list` qui prend un entier $n$ en paramètre et renvoie une permutation aléatoire des entiers entre 0 et $n-1$.

In [ ]:
def random_list(n):
    s = list(range(n))
    melanger(s)
    return s

In [ ]:
print(random_list(10))

Voici enfin le bogo-tri. La fonction `bogo_tri` prend en paramètre une liste $s$ et trie cette liste sur place. La fonction renvoie le nombre de mélanges effectués.

In [ ]:
def bogo_tri(s):
    cpt = 0
    while not(est_triee(s)):
        cpt += 1
        melanger(s)
    return cpt

Testons.

In [ ]:
s = random_list(6)
print(bogo_tri(s))
print(s)

## 2. Un peu de théorie

Dans toute la suite, $n\in\N$ est un entier naturel fixé. On s'intéresse au bogo-tri de listes de longueur $n$. Dans notre « analyse », nous supposerons que les éléments des listes sont distincts deux à deux.

### 2.1 Une variable aléatoire

Nous nous intéresserons exclusivement ici au nombre de mélanges nécessaires pour trier une liste. Un mélange de la liste $s$ de longueur $n$ trie la liste avec une probabilité

$$p=\frac 1 {n!}$$

On peut modéliser le bogo-tri par une suite $(M_k)_{k\in\N}$ de variables de Bernoulli indépendantes de paramètre $p$, définies sur un même espace probabilisé $(\Omega,\mathcal T,\Pr)$. La variable aléatoire qui nous intéresse est la v.a. $T:\Omega\too\N\cup\{+\infty\}$, définie pour tout $\omega\in\Omega$ par

$$T(\omega)=\min\{k\in\N:M_k(\omega)=1\}$$

en convenant que ce minimum est $+\infty$ si l'ensemble est vide.

La v.a. $T$ suit une *loi géométrique* de paramètre $p$. Plus précisément, pour tout $k\in\N$, on a

$$\{T=k\}=\{M_0=0,M_1=0,\ldots,M_{k-1}=0,M_k=1\}$$

Par l'indépendance des $M_i$,

$$\Pr(T=k)=\Pr(M_0=0)\Pr(M_1=0)\ldots\Pr(M_{k-1}=0)\Pr(M_k=1)=(1-p)^kp$$

Il nous reste à déterminer $\Pr(T=+\infty)$. Remarquons que

$$\sum_{k=0}^\infty \Pr(T=k)=p\sum_{k=0}^\infty(1-p)^k=\frac p{1-(1-p)}=1$$

Ainsi,

$$\Pr(T=+\infty)=1-\sum_{k=0}^\infty \Pr(T=k)=1-1=0$$

Ceci est rassurant. La fonction de bogo-tri **peut** ne pas terminer. Dit plus lapidairement, sa complexité en pire cas est $+\infty$. Cela dit, la probabilité que la fonction ne termine pas est 0.

Pour parler savamment, l'algorithme du bogo-tri est un *algorithme probabiliste*. Il peut ne pas terminer (avec, certes, une probabilité nulle), mais si il termine alors il renvoie la bonne réponse. Nous avons là un *algorithme de Las Vegas*.

Voyons maintenant quelle est la complexité en moyenne du bogo-tri, en termes de nombre de mélanges. En clair, déterminons l'espérance de $T$.

### 1.2 L'espérance de $T$

La *série génératrice* de $T$ est

$$F(x)=\sum_{k=0}^\infty \Pr(T=k)x^k=p\sum_{k=0}^\infty(1-p)^kx^k$$

Nous avons là une série entière qui a pour rayon de convergence 

$$R=\frac 1 {1-p}>1$$

On reconnaît dans $F(x)$ une série géométrique de raison $(1-p)x$. On a donc pour tout $x\in ]-R,R[$,

$$F(x)=\frac p{1-x(1-p)}$$

De là, par une dérivation terme à terme (le lecteur ouvrira son cours sur les séries entières),

$$F'(x)=\sum_{k=1}^\infty k\Pr(T=k)x^{k-1}$$

Remarquons maintenant que

$$F'(1)=\sum_{k=1}^\infty k\Pr(T=k)=\sum_{k=0}^\infty k\Pr(T=k)=E(T)$$

On a aussi, en prenant l'expression simplifiée de $F(x)$,

$$F'(x)=\frac {p(1-p)}{(1-x(1-p))^2}$$

et donc

$$E(T)=\frac 1 p - 1=n!-1$$

Imaginons que nous soyons capables de faire un milliard de mélanges par seconde. En combien de temps pouvons-nous espérer bogo-trier une liste de taille 20 ?

In [ ]:
(math.factorial(20) - 1) / 1e9 / 3600 / 365

Il nous faudra attendre 1850 ans. 

### 2.3 La variance de $T$

Une nouvelle dérivation de $F'(x)$ (cours sur les séries entières !) donne 

$$F''(x)=\sum_{k=2}^\infty k(k-1)\Pr(T=k)x^{k-2}$$

De là,

$$F''(1)=\sum_{k=2}^\infty k(k-1)\Pr(T=k)=\sum_{k=0}^\infty k(k-1)\Pr(T=k)=E(T^2)-E(T)$$

Ainsi, en nous souvenant que $F'(1)=E(T)$,

$$V(T)=E(T^2)-E(T)^2=F''(1)+F'(1)-F'(1)^2$$

En dérivant l'expression simplifiée de $F'(x)$, il vient

$$F''(x)=\frac{2p(1-p)^2}{(1-x(1-p))^3}$$

et donc

$$F''(1)=2\left(\frac 1 p - 1\right)^2$$

d'où, facilement,

$$V(T)=\frac 1 p\left(\frac 1 p - 1\right)=n!(n!-1)$$

### 2.4 Le vrai temps d'attente

L'espoir c'est bien, mais qu'en est-il dans la réalité ? Remarquons que l'écart-type de $T$, $\sigma(T)$, vaut

$$\sigma(T)=\sqrt{n!(n!-1)}>n!-1=E(T)$$

Un écart-type plus grand que l'espérance, c'est le signe que notre variable aléatoire $T$ est vraiment très aléatoire. Tentons un petit calcul.

Soit $t\in\N$. Quelle est la probabilité que $T$ soit au moins égal à $t$ ? On a

$$\Pr(T\ge t)=\sum_{k=t}^\infty \Pr(T=k)=p\sum_{k=t}^\infty(1-p)^k=p(1-p)^t$$


Soit maintenant $\epsilon>0$. Pour quelles valeurs de $t$ a-t-on $\Pr(T\ge t)\le\epsilon$ ? Dit autrement, en prenant par exemple $\epsilon=\frac 1 {100}$, pour quelles valeurs de $t$ a-t-on 99% de chances de trier notre liste en moins de $t$ mélanges ?

C'est le cas si et seulement si $p(1-p)^t\le\epsilon$, c'est à dire, en passant aux logarithmes,

$$t\ge\frac{\ln \epsilon -\ln p}{\ln(1-p)}$$

Ou encore, en nous souvenant que $p=1/n!$,

$$t\ge\frac {\ln\epsilon+\ln n!}{\ln\left(1-\frac 1 {n!}\right)}$$

In [ ]:
def phi(n, eps):
    f = math.factorial(n)
    return (math.log(eps) - math.log(f)) / math.log(1 - 1 / f)

Le graphique ci-dessous nous confirme que le bogo-tri est un *très mauvais* algorithme. En noir, le nombre de mélanges nécessaires pour trier avec 99% de chances de réussite. En rouge, l'espérance, forcément déçue.

In [ ]:
eps = 0.01
xs = range(2, 15)
ys = [phi(x, eps) for x in xs]
zs = [math.factorial(x) - 1 for x in xs]
plt.semilogy(xs, ys, 'k')
plt.semilogy(xs, zs, 'r')
plt.grid()

## 3. Une expérience statistique

### 3.1 Une simulation

La fonction `stats` effectue $m$ bogo-tris sur une liste aléatoire de longueur $n$. Elle renvoie un dictionnaire dont les clés sont les nombres de mélanges constatés lors des $m$ bogo-tris et les valeurs sont, pour chacun de ces nombres, le nombre moyen de bogo-tris ayant nécessité ce nombre de mélanges.

In [ ]:
def stats(n, m):
    st = {}
    for i in range(m):
        s = list(range(n))
        melanger(s)
        c = bogo_tri(s)
        if c in st: st[c] += 1
        else: st[c] = 1
    for x in st:
        st[x] = st[x] / m
    return st

Juste pour vérifier la correction des calculs faits plus haut ...

In [ ]:
def moment(st, k):
    s = 0
    for x in st:
        s += st[x] * x ** k
    return s

In [ ]:
def esperance(st): return moment(st, 1)
def variance(st): return moment(st, 2) - moment(st, 1) ** 2

In [ ]:
st = stats(4, 1000)

In [ ]:
print(esperance(st))
print(variance(st))

In [ ]:
f = math.factorial(4)
print(f - 1)
print(f * (f - 1))

Nos statistiques s'accordent pas trop mal avec la théorie.

### 3.2 Représentation graphique

Il nous reste à afficher graphiquement tout cela. Ci-dessous, les points noirs sont les moyennes constatées. La courbe rouge est la courbe théorique des probabilités $\Pr(T=k)$.

Nos calculs théoriques nous incitent à la prudence. Nous allons donc bogo-trier des listes de taille 4.

In [ ]:
n = 4
f = math.factorial(n)
p = 1 / f
print('Espérance  : %d' % (f - 1))
print('Écart-type : %.3f' % (math.sqrt(f * (f - 1))))
st = stats(n, 10000)
xs = [x for x in st]
xs.sort()
ys = [st[x] for x in xs]
zs = [(1 - p) ** x * p for x in xs]
plt.plot(xs, ys, 'ok')
plt.plot(xs, zs, 'r')
plt.grid()

**Conclusion.** Évitez d'utiliser le bogo-tri. Parce que franchement, faire 150 comparisons pour trier 4 objets c'est un peu beaucoup😀.

**Bibliographie**

- H. Gruber, M. Holzer, O. Ruepp, Sorting the Slow Way: An Analysis of Perversely Awful Randomized Sorting Algorithms. Volume 4475 of Lecture Notes in Computer Science, pages 183-197, Springer, 2007.
- A. Broder, J. Stolfi, Pessimal Algorithms. SIGACT News, 16(3):49-53, 1984.